In [1]:
import pandas as pd
import numpy as np
import os
from collections import Counter
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA
from sklearn.metrics.pairwise import cosine_similarity
import random

In [2]:
ingresync_recipe = pd.read_csv('/opt/ml/Recipe_Project/Recipe_datasets/recipe_data_final.csv')

In [3]:
ingresync_recipe['ingredients'] = ingresync_recipe['ingredients'].apply(eval)
ingresync_recipe['ingredient_quantity'] = ingresync_recipe['ingredient_quantity'].apply(eval)
ingresync_recipe['process'] = ingresync_recipe['process'].apply(eval)

In [4]:
ingresync_recipe

recipeid                                            title  \
0        6912734                버섯으로 관자 느낌 내는 방법! 새송이버섯간장버터구이 만들기   
1        6843136                              달콤 짭조름♡ 떡 베이컨 간장조림♡   
2        7002443                     쫄깃한 식감과 버터의 풍미가 느껴지는 닭고기스테이크   
3        6996297                       고구마떡 고구마씨를 말릴 수 있는 위험한 레시피   
4        6885909                              【간단반찬】꽈리고추 햄볶음 만들기~   
...          ...                                              ...   
120824   7004885                초간단 간식 편스토랑레시피 최귀화 말린도토리묵튀김 건조묵튀김   
120825   7004887  어묵국 만드는법 시원한 어묵국물 끓이는법 오뎅국 레시피 사각 어묵 요리 충무김밥 단짝   
120826   7004898                           상큼한 오징어오이초무침으로 여름반찬 끝!   
120827   7004906                         식단관리에 좋은 저탄고지, 야채돌돌삼겹야채찜   
120828   7004927                                    오리고기 샌드위치 레시피   

               cook quantity    time level  \
0       새송이버섯간장버터구이      1인분  15분 이내   아무나   
1          떡베이컨간장조림      3인분   5분 이내   아무나   
2           닭고기스테이크      2인분  30분 이내   아무나   
3              고구마떡      2인분  20분 이내   아무나   
4           꽈리고추햄볶음      3인분  10분 이내   아무나   
...             ...      ...     ...   ...   
120824        건조묵튀김      2인분  15분 이내    초급   
120825          어묵국      4인분  30분 이내   아무나   
120826     오징어오이초무침      2인분  15분 이내   아무나   
120827        삼겹야채찜      2인분  90분 이내    초급   
120828     오리고기샌드위치      1인분  20분 이내    초급   

                                              ingredients  \
0                        [새송이버섯, 버터, 어린잎채소, 간장, 맛술, 올리고당]   
1                           [베이컨, 대파, 떡, 간장, 참기름, 물엿, 기름]   
2       [닭다리살 정육, 소금, 후추, 바질가루, 버터, 올리브유, 감자, 아스파라거스, ...   
3                            [고구마, 설탕, 감자전분, 모짜렐라치즈, 식용유]   
4             [꽈리고추, 햄, 양파, 진간장, 굴소스, 마늘, 올리고당, 식용유, 참기름]   
...                                                   ...   
120824                          [말린 도토리묵, 볶은 콩가루, 꿀, 식용유]   
120825  [사각 어묵, 무, 물, 국간장, 참치액, 소금, 대파, 무, 대파뿌리, 디포리, ...   
120826  [오징어, 오이, 대파, 당근, 통깨, 고춧가루 숟가락, 설탕 숟가락, 다진마늘, ...   
120827  [대패삼겹살, 당근, 부추, 팽이버섯, 유자청, 다진마늘, 맛술, 파, 청양고추, ...   
120828         [오리고기, 호밀식빵, 계란, 토마토, 양상추, 치즈, 마요네즈, 칠리소스]   

                                      ingredient_quantity  \
0                               [2개, 30g, , 1T, 1T, 1/2T]   
1                                          [, , , , , , ]   
2       [300g, 약간, 약간, 약간, 1숟가락, 3숟가락, , , 3숟가락, 3숟가락,...   
3                                [1개, 5큰술, 3큰술, 적당량, 3큰술]   
4             [20개, 140g, 1/2개, 2T, 1/2T, 3쪽, 2T, 1T, 1T]   
...                                                   ...   
120824                               [120g, 3스푼, 3스푼, 약간]   
120825  [1봉지, 300g, 1.8L, 2T, 1T, 1T, , 4조각, 2개, 1마리, ...   
120826  [1마리, 1개, 1/2줄기, 1/3개, 약간, 6g, 6g, 1/2숟가락10g, ...   
120827  [300g, 1/2, 100g, 1개, 4T, 2T, 1T, 1개, 2개, 2개, ...   
120828             [100g, 2장, 1개, 1/2개, 3장, 1장, 1스푼, 2스푼]   

                                                  process    view  
0       [버섯의 밑동과 갓을 잘라낸 뒤, 3~4등분 한다, 자른버섯의 양면에 칼집을 낸다,...  324000  
1       [대파에 떡국떡 (가래떡, 떡볶이떡) 베이컨, 기름두르고 볶듯구워요.(튀기듯하면 더...  196000  
2       [닭다리살은 소금, 후추, 바질가루를 뿌려 재료 준비하는 동안 재워요., 감자, 아...    1152  
3       [고구마 1개 10~15분간 뚜껑을 닫고\n찜기에 쪄주세요 \n(찬물에 처음부터 함...    5102  
4       [꽈리고추(20개)는 먹기좋게 3등분해서 썰어 주시구요~, 햄(140g)도 썰어 주...  164000  
...                                                   ...     ...  
120824  [재료 준비해 주세요~, 180도 예열한 기름에 건조 도토리묵을 넣고 튀겨 주세요~...      43  
120825  [육수팩을 준비합니다. 다시백에 다시마, 디포리(밴댕이), 무, 멸치, 생강, 대파...      69  
120826  [오징어는 안쪽에 칼집모양을 낸 뒤 먹기 좋은 크기로 잘라요., 오이는 반으로 갈라...     182  
120827  [대패 삼겹살은 한 줄 씩 펴서 후추와 소금으로 밑간을 해주세요, 당근, 부추, 팽...      95  
120828  [토마토를 원형으로 썰어 물기를 닦아주세요., 팬에 계란후라이를 해서 따로 한쪽에 ...      13  

[120829 rows x 10 columns]

In [5]:
ingredients_origin = set(np.concatenate(ingresync_recipe['ingredients']))

In [6]:
#형규형이 재료에 빈 문자열 빼주면 이거도 없애
ingredients_origin.discard('')
ingredients_origin = set(ingredients_origin)

In [7]:
len(ingredients_origin)

45669

In [8]:
ingredients_origin

{'육수바리스타 멸치',
 '조개젓 듬뿍',
 '그라나파나노치즈',
 '손질된 오징어',
 '진미채 볶음',
 '참기름 숟가락',
 '쌀발효 소금',
 '찹쌀호떡믹스 또는 호떡믹스',
 '생 모짜렐라 슬라이스',
 '매운 김치만두',
 '한우 불고기감',
 '다진 이탈리안파슬리',
 '파채양념',
 '마른 건고추매운것',
 '동원 알감자캔',
 '다담냉이된장찌개양념',
 '오가피 순',
 '주꾸미',
 '중국식만능소스',
 '오뚜기 고소한 참기름',
 '새싹 보리',
 '스팸 종이컵',
 '돼지고기 앞다리살 슬라이스',
 '맛술생강즙',
 '다담강된장비빔양념',
 '전복 왕왕특',
 '블랙올리브캔',
 '폰타나수프',
 '순한 라면스프',
 '납작 어묵',
 '고체 카레 큐브',
 '청포도 적포도',
 '팽이버섯전',
 '돼지고기등심 다짐육',
 '화이트와인식초',
 '국물용 멸치가루',
 '삶은 시래기 꼭 짠 것',
 '참드림 밥',
 '영양부추쪽파',
 '계란 각',
 '꼬막삶은물',
 '통삼겹살또는 편육',
 '완두맛어묵',
 '매운양념치킨소스',
 '국탕용 어묵',
 '돼지고기갈비살',
 '마요 참치',
 '가지절임용 소금',
 '삶은 땅콩',
 '들깻가루 듬뿍',
 '통삼겹살혹은 수육용 돼지고기',
 '대파 조금',
 '햄  스팸',
 '육공방마일드갈릭생소시지',
 '초콜릿칩',
 '말린곤드레나물',
 '대추씨 끓인 물',
 '고구마감자',
 '아가베 시럽올리고 당',
 '토마토큰 사이즈',
 '찹쌀누룽지향수과바',
 '시판 육수',
 '남은 호떡잼믹스',
 '냉이 나물무침',
 '냉동 중면',
 '가래떡떡볶이떡',
 '사과식초과일식초',
 '파인애플 통조림 슬라이스',
 '통통한 가지',
 '감자 어린이주먹크기',
 '양배추등',
 '다듬은 참나물',
 '치커리 잎',
 '백설돼지갈비양념',
 '통깨들깨가루',
 '바닐라익스트랙',
 '된장 큰술',
 '목우촌 오메가 훈제오리 슬라이스',
 '버섯넣고싶은 걸로',
 '청양고추나 홍고추',
 '해물믹스

In [9]:
def remove_whitespace_from_keys(dictionary):
    for key in list(dictionary.keys()):
        updated_key = key.replace(" ", "")
        if updated_key != key:
            dictionary[updated_key] = dictionary.pop(key)
    return dictionary

In [10]:
counter = Counter(val for sublist in ingresync_recipe['ingredients'] for val in sublist)
ingredients_counts = dict(counter)
ingredients_counts

{'새송이버섯': 2351,
 '버터': 8675,
 '어린잎채소': 351,
 '간장': 27008,
 '맛술': 12747,
 '올리고당': 11955,
 '베이컨': 2587,
 '대파': 25552,
 '떡': 469,
 '참기름': 31517,
 '물엿': 4512,
 '기름': 1308,
 '닭다리살 정육': 16,
 '소금': 41059,
 '후추': 22556,
 '바질가루': 315,
 '올리브유': 4439,
 '감자': 7102,
 '아스파라거스': 348,
 '케찹': 1900,
 '고구마': 1487,
 '설탕': 39571,
 '감자전분': 606,
 '모짜렐라치즈': 1617,
 '식용유': 14110,
 '꽈리고추': 1295,
 '햄': 1533,
 '양파': 37812,
 '진간장': 8622,
 '굴소스': 6824,
 '마늘': 13107,
 '달걀': 9746,
 '청양고추': 14506,
 '쪽파 또는 대파': 25,
 '멸치육수': 1412,
 '고추장': 14411,
 '고춧가루': 20507,
 '깨': 5039,
 '닭봉': 150,
 '파프리카': 3065,
 '꿀': 4233,
 '후추가루': 1792,
 '팽이버섯': 2366,
 '통깨': 16493,
 '물': 28748,
 '또띠아': 729,
 '참치캔': 791,
 '치즈': 1432,
 '토마토소스': 844,
 '차돌박이': 438,
 '깻잎': 3902,
 '숙주나물': 359,
 '미소된장': 85,
 '마요네즈': 5882,
 '다진마늘': 31951,
 '단무지': 1055,
 '대파 손가락 길이': 3,
 '고추가루': 7352,
 '참기름 또는 들기름': 64,
 '오이고추': 261,
 '쌈장': 418,
 '칵테일 새우': 104,
 '식초': 11316,
 '프랑크소시지': 60,
 '마늘쫑': 721,
 '스팸': 1359,
 '계란': 13352,
 '느타리버섯': 1769,
 '밥': 7557,
 '참깨': 1588,
 '진미

In [11]:
keys_with_specific_value = [key for key, value in ingredients_counts.items() if value == 1]
len(keys_with_specific_value)

31877

In [12]:
ingredients_counts['치즈']

1432

In [13]:
ingresync_recipe

recipeid                                            title  \
0        6912734                버섯으로 관자 느낌 내는 방법! 새송이버섯간장버터구이 만들기   
1        6843136                              달콤 짭조름♡ 떡 베이컨 간장조림♡   
2        7002443                     쫄깃한 식감과 버터의 풍미가 느껴지는 닭고기스테이크   
3        6996297                       고구마떡 고구마씨를 말릴 수 있는 위험한 레시피   
4        6885909                              【간단반찬】꽈리고추 햄볶음 만들기~   
...          ...                                              ...   
120824   7004885                초간단 간식 편스토랑레시피 최귀화 말린도토리묵튀김 건조묵튀김   
120825   7004887  어묵국 만드는법 시원한 어묵국물 끓이는법 오뎅국 레시피 사각 어묵 요리 충무김밥 단짝   
120826   7004898                           상큼한 오징어오이초무침으로 여름반찬 끝!   
120827   7004906                         식단관리에 좋은 저탄고지, 야채돌돌삼겹야채찜   
120828   7004927                                    오리고기 샌드위치 레시피   

               cook quantity    time level  \
0       새송이버섯간장버터구이      1인분  15분 이내   아무나   
1          떡베이컨간장조림      3인분   5분 이내   아무나   
2           닭고기스테이크      2인분  30분 이내   아무나   
3              고구마떡      2인분  20분 이내   아무나   
4           꽈리고추햄볶음      3인분  10분 이내   아무나   
...             ...      ...     ...   ...   
120824        건조묵튀김      2인분  15분 이내    초급   
120825          어묵국      4인분  30분 이내   아무나   
120826     오징어오이초무침      2인분  15분 이내   아무나   
120827        삼겹야채찜      2인분  90분 이내    초급   
120828     오리고기샌드위치      1인분  20분 이내    초급   

                                              ingredients  \
0                        [새송이버섯, 버터, 어린잎채소, 간장, 맛술, 올리고당]   
1                           [베이컨, 대파, 떡, 간장, 참기름, 물엿, 기름]   
2       [닭다리살 정육, 소금, 후추, 바질가루, 버터, 올리브유, 감자, 아스파라거스, ...   
3                            [고구마, 설탕, 감자전분, 모짜렐라치즈, 식용유]   
4             [꽈리고추, 햄, 양파, 진간장, 굴소스, 마늘, 올리고당, 식용유, 참기름]   
...                                                   ...   
120824                          [말린 도토리묵, 볶은 콩가루, 꿀, 식용유]   
120825  [사각 어묵, 무, 물, 국간장, 참치액, 소금, 대파, 무, 대파뿌리, 디포리, ...   
120826  [오징어, 오이, 대파, 당근, 통깨, 고춧가루 숟가락, 설탕 숟가락, 다진마늘, ...   
120827  [대패삼겹살, 당근, 부추, 팽이버섯, 유자청, 다진마늘, 맛술, 파, 청양고추, ...   
120828         [오리고기, 호밀식빵, 계란, 토마토, 양상추, 치즈, 마요네즈, 칠리소스]   

                                      ingredient_quantity  \
0                               [2개, 30g, , 1T, 1T, 1/2T]   
1                                          [, , , , , , ]   
2       [300g, 약간, 약간, 약간, 1숟가락, 3숟가락, , , 3숟가락, 3숟가락,...   
3                                [1개, 5큰술, 3큰술, 적당량, 3큰술]   
4             [20개, 140g, 1/2개, 2T, 1/2T, 3쪽, 2T, 1T, 1T]   
...                                                   ...   
120824                               [120g, 3스푼, 3스푼, 약간]   
120825  [1봉지, 300g, 1.8L, 2T, 1T, 1T, , 4조각, 2개, 1마리, ...   
120826  [1마리, 1개, 1/2줄기, 1/3개, 약간, 6g, 6g, 1/2숟가락10g, ...   
120827  [300g, 1/2, 100g, 1개, 4T, 2T, 1T, 1개, 2개, 2개, ...   
120828             [100g, 2장, 1개, 1/2개, 3장, 1장, 1스푼, 2스푼]   

                                                  process    view  
0       [버섯의 밑동과 갓을 잘라낸 뒤, 3~4등분 한다, 자른버섯의 양면에 칼집을 낸다,...  324000  
1       [대파에 떡국떡 (가래떡, 떡볶이떡) 베이컨, 기름두르고 볶듯구워요.(튀기듯하면 더...  196000  
2       [닭다리살은 소금, 후추, 바질가루를 뿌려 재료 준비하는 동안 재워요., 감자, 아...    1152  
3       [고구마 1개 10~15분간 뚜껑을 닫고\n찜기에 쪄주세요 \n(찬물에 처음부터 함...    5102  
4       [꽈리고추(20개)는 먹기좋게 3등분해서 썰어 주시구요~, 햄(140g)도 썰어 주...  164000  
...                                                   ...     ...  
120824  [재료 준비해 주세요~, 180도 예열한 기름에 건조 도토리묵을 넣고 튀겨 주세요~...      43  
120825  [육수팩을 준비합니다. 다시백에 다시마, 디포리(밴댕이), 무, 멸치, 생강, 대파...      69  
120826  [오징어는 안쪽에 칼집모양을 낸 뒤 먹기 좋은 크기로 잘라요., 오이는 반으로 갈라...     182  
120827  [대패 삼겹살은 한 줄 씩 펴서 후추와 소금으로 밑간을 해주세요, 당근, 부추, 팽...      95  
120828  [토마토를 원형으로 썰어 물기를 닦아주세요., 팬에 계란후라이를 해서 따로 한쪽에 ...      13  

[120829 rows x 10 columns]

In [14]:
ingredients_origin = list(ingredients_origin)

In [15]:
list(ingredients_origin).index('버터')

16285

In [16]:
ingredients_counts['돼지고기']

2089

In [17]:
ingredients_counts

{'새송이버섯': 2351,
 '버터': 8675,
 '어린잎채소': 351,
 '간장': 27008,
 '맛술': 12747,
 '올리고당': 11955,
 '베이컨': 2587,
 '대파': 25552,
 '떡': 469,
 '참기름': 31517,
 '물엿': 4512,
 '기름': 1308,
 '닭다리살 정육': 16,
 '소금': 41059,
 '후추': 22556,
 '바질가루': 315,
 '올리브유': 4439,
 '감자': 7102,
 '아스파라거스': 348,
 '케찹': 1900,
 '고구마': 1487,
 '설탕': 39571,
 '감자전분': 606,
 '모짜렐라치즈': 1617,
 '식용유': 14110,
 '꽈리고추': 1295,
 '햄': 1533,
 '양파': 37812,
 '진간장': 8622,
 '굴소스': 6824,
 '마늘': 13107,
 '달걀': 9746,
 '청양고추': 14506,
 '쪽파 또는 대파': 25,
 '멸치육수': 1412,
 '고추장': 14411,
 '고춧가루': 20507,
 '깨': 5039,
 '닭봉': 150,
 '파프리카': 3065,
 '꿀': 4233,
 '후추가루': 1792,
 '팽이버섯': 2366,
 '통깨': 16493,
 '물': 28748,
 '또띠아': 729,
 '참치캔': 791,
 '치즈': 1432,
 '토마토소스': 844,
 '차돌박이': 438,
 '깻잎': 3902,
 '숙주나물': 359,
 '미소된장': 85,
 '마요네즈': 5882,
 '다진마늘': 31951,
 '단무지': 1055,
 '대파 손가락 길이': 3,
 '고추가루': 7352,
 '참기름 또는 들기름': 64,
 '오이고추': 261,
 '쌈장': 418,
 '칵테일 새우': 104,
 '식초': 11316,
 '프랑크소시지': 60,
 '마늘쫑': 721,
 '스팸': 1359,
 '계란': 13352,
 '느타리버섯': 1769,
 '밥': 7557,
 '참깨': 1588,
 '진미

In [18]:
len(ingredients_origin)

45669

In [19]:
ingredients_counts['돼지고기']/len(ingredients_origin)

0.04574218835533951

In [20]:
sorted_ingredients_counts = dict(sorted(ingredients_counts.items(), key=lambda x: -x[1]))
sorted_ingredients_counts

{'소금': 41059,
 '설탕': 39571,
 '양파': 37812,
 '다진마늘': 31951,
 '참기름': 31517,
 '물': 28748,
 '간장': 27008,
 '대파': 25552,
 '후추': 22556,
 '고춧가루': 20507,
 '통깨': 16493,
 '당근': 15162,
 '청양고추': 14506,
 '고추장': 14411,
 '식용유': 14110,
 '계란': 13352,
 '마늘': 13107,
 '맛술': 12747,
 '올리고당': 11955,
 '식초': 11316,
 '달걀': 9746,
 '버터': 8675,
 '진간장': 8622,
 '국간장': 7806,
 '밥': 7557,
 '고추가루': 7352,
 '홍고추': 7196,
 '우유': 7177,
 '감자': 7102,
 '다진 마늘': 6851,
 '굴소스': 6824,
 '두부': 6549,
 '들기름': 6434,
 '깨소금': 6338,
 '무': 5980,
 '된장': 5973,
 '마요네즈': 5882,
 '후춧가루': 5825,
 '오이': 5768,
 '파': 5460,
 '깨': 5039,
 '매실청': 4519,
 '물엿': 4512,
 '올리브유': 4439,
 '쪽파': 4338,
 '애호박': 4313,
 '꿀': 4233,
 '매실액': 4185,
 '양배추': 4127,
 '밀가루': 4097,
 '청주': 4079,
 '부추': 4014,
 '깻잎': 3902,
 '표고버섯': 3425,
 '콩나물': 3254,
 '다시마': 3245,
 '식빵': 3227,
 '멸치액젓': 3204,
 '김치': 3178,
 '새우젓': 3067,
 '파프리카': 3065,
 '레몬즙': 3018,
 '생강': 2983,
 '액젓': 2926,
 '부침가루': 2713,
 '통마늘': 2711,
 '박력분': 2694,
 '베이컨': 2587,
 '올리브오일': 2525,
 '파슬리가루': 2515,
 '다진파': 2493,
 '팽이버섯':

In [21]:
for key, value in list(sorted_ingredients_counts.items()):
    print(key, value)

소금 41059
설탕 39571
양파 37812
다진마늘 31951
참기름 31517
물 28748
간장 27008
대파 25552
후추 22556
고춧가루 20507
통깨 16493
당근 15162
청양고추 14506
고추장 14411
식용유 14110
계란 13352
마늘 13107
맛술 12747
올리고당 11955
식초 11316
달걀 9746
버터 8675
진간장 8622
국간장 7806
밥 7557
고추가루 7352
홍고추 7196
우유 7177
감자 7102
다진 마늘 6851
굴소스 6824
두부 6549
들기름 6434
깨소금 6338
무 5980
된장 5973
마요네즈 5882
후춧가루 5825
오이 5768
파 5460
깨 5039
매실청 4519
물엿 4512
올리브유 4439
쪽파 4338
애호박 4313
꿀 4233
매실액 4185
양배추 4127
밀가루 4097
청주 4079
부추 4014
깻잎 3902
표고버섯 3425
콩나물 3254
다시마 3245
식빵 3227
멸치액젓 3204
김치 3178
새우젓 3067
파프리카 3065
레몬즙 3018
생강 2983
액젓 2926
부침가루 2713
통마늘 2711
박력분 2694
베이컨 2587
올리브오일 2525
파슬리가루 2515
다진파 2493
팽이버섯 2366
새송이버섯 2351
사과 2291
생크림 2210
미림 2201
간마늘 2175
참치액 2121
어묵 2105
돼지고기 2089
소고기 2085
토마토 2027
생강가루 2011
오징어 1983
양조간장 1945
베이킹파우더 1912
새우 1910
케찹 1900
튀김가루 1888
굵은소금 1873
가지 1800
후추가루 1792
멸치 1779
느타리버섯 1769
통후추 1718
소주 1703
시금치 1673
들깨가루 1662
호박 1627
모짜렐라치즈 1617
참깨 1588
방울토마토 1544
햄 1533
고구마 1487
월계수잎 1486
빵가루 1466
닭가슴살 1460
다진생강 1442
케첩 1434
치즈 1432
멸치육

In [22]:
def count_keys_with_value_above_threshold(dictionary, threshold):
    count = 0
    for value in dictionary.values():
        if value >= threshold:
            count += 1
    return count

In [23]:
# 카테고리 컬럼 문자열 변환
cate_recipe = pd.read_csv('/opt/ml/Recipe_Project/Recipe_datasets/cate_data_final.csv')
cate_recipe['cat1'] = cate_recipe['cat1'].astype(str)
cate_recipe['cat2'] = cate_recipe['cat2'].astype(str)
cate_recipe['cat3'] = cate_recipe['cat3'].astype(str)
cate_recipe['cat4'] = cate_recipe['cat4'].astype(str)

# 범주형 열에 대해 One-Hot Encoding 수행

df_encoded = pd.get_dummies(cate_recipe[['cat1', 'cat2', 'cat3', 'cat4']])

# recipeid 컬럼과 One-Hot Encoding 결과 병합
df_merged = pd.concat([cate_recipe['recipeid'], df_encoded], axis=1)

# 사전 생성
result_dict = dict(zip(df_merged['recipeid'], df_merged.iloc[:, 1:].values.tolist()))


In [24]:
def merge_dicts(dict1, dict2):
    merged_dict = dict1.copy()
    for key, value in dict2.items():
        if key in merged_dict:
            merged_dict[key] = np.concatenate((merged_dict[key], np.array(value)))
        else:
            merged_dict[key] = np.array(value)
    return merged_dict

In [25]:

ingredient_sparse_vector_collect = {}
ingredient_dense_vector_collect = {}
threshold = 16
ingredients_threshold_len = count_keys_with_value_above_threshold(ingredients_counts, threshold)
ingredients_origin_len = len(ingredients_origin)
sorted_ingredients_counts_list = list(sorted_ingredients_counts.keys())[:ingredients_threshold_len]

pca = PCA(n_components=128)


for index, row in ingresync_recipe.iterrows():
    ingredient_sparse_vector = [0] * ingredients_threshold_len

    #재료 중복 제거
    set_row = list(set(row['ingredients']))

    #재료 사이 공백 제거 -> 하니까 살짝 오류가 생기네.. 새송이버섯 -> 새송이 버섯 이런것도 있어가지고 함부로 줄일 수가 없다..
    #set_row = [string.replace(" ", "") for string in set_row_c if isinstance(string, str)]


    for r in set_row:
        if(ingredients_counts[r] >= threshold):
            if(r in row['cook']):
                ingredient_sparse_vector[sorted_ingredients_counts_list.index(r)] = (1 - ingredients_counts[r]/ingredients_origin_len) * 10
            else:
                ingredient_sparse_vector[sorted_ingredients_counts_list.index(r)] = (1 - ingredients_counts[r]/ingredients_origin_len)

    ingredient_sparse_vector_collect[row['recipeid']] = ingredient_sparse_vector

pca.fit(np.array(list(ingredient_sparse_vector_collect.values())))

ingredient_dense_vector_collect = pca.transform(np.array(list(ingredient_sparse_vector_collect.values())))
ingredient_dense_vector_collect_dict = {key: ingredient_dense_vector_collect[i] for i, key in enumerate(ingredient_sparse_vector_collect)}
ingredient_dense_vector_collect = merge_dicts(ingredient_dense_vector_collect_dict, result_dict)
    

In [26]:
ingredient_dense_vector_collect

{6912734: array([-4.31454804e-01, -3.36718866e-01, -1.75884145e-01, -2.23306806e-01,
        -4.37061261e-01, -2.03194254e-01, -3.46319452e-01, -4.93789491e-01,
        -3.62257725e-01, -5.36621566e-01, -1.82021106e-01, -2.82429621e-01,
        -3.14235778e-01, -1.90406457e-02, -1.80290589e-01,  1.05456194e-01,
        -8.04039923e-01, -8.44133258e-01, -7.11495170e-01, -1.40486883e+00,
         2.65695956e+00,  1.09732335e-01,  7.75254889e-01,  7.92029827e-01,
         1.91126959e-01, -8.52062701e-01,  2.02955461e-01,  1.22586071e-02,
        -1.09595023e+00, -1.07202807e+00, -2.38661200e+00,  4.84332603e+00,
         3.85587841e+00,  8.76067919e-01,  1.65967745e-01,  3.58912524e-01,
        -2.78646765e-02, -7.90227397e-01, -6.82889262e-01, -4.09988603e-02,
         1.98463755e-01,  6.82006834e-02, -2.30421097e+00,  7.70970402e-01,
        -1.12196382e+00, -1.70697819e-01,  5.43512245e-01, -7.40420901e-02,
         4.25699462e-01, -9.74604004e-01, -7.12867962e-01, -1.77815758e-01,
   

In [30]:
list(ingredient_dense_vector_collect.values())[0].shape[0]

189

In [ ]:
len(ingredient_dense_vector_collect[6912734])

189

In [ ]:
def get_top_similar_recipes(query_vector, recipe_dict, top_k=10):
    similarities = []
    query_vector = np.array(query_vector).reshape(1, -1)

    for recipe_number, dense_vector in recipe_dict.items():
        dense_vector = np.array(dense_vector).reshape(1, -1)
        similarity = cosine_similarity(query_vector, dense_vector)[0, 0]
        similarities.append((recipe_number, similarity))

    similarities.sort(key=lambda x: x[1], reverse=True)
    top_similar_recipes = similarities[:top_k]

    return top_similar_recipes

In [ ]:
#user_ingredient = ['돼지고기','두부','멸치','오이','당근','양파','진간장','국간장','마늘','소금','새우젓','계란','김치','감자']
#user_ingredient = ['스파게티','간장','토마토소스','케찹','마요네즈','계란','마늘','소금','고등어','당근','오이지']
user_ingredient = ['돼지고기', '베이컨', '소금', '마늘', '닭가슴살', '양파', '간장', '설탕', '대파']

user_ingredient_sparse_vector = [0] * ingredients_threshold_len
invalid_ingredients = []

#재료사이 공백 제거
user_ingredient = [string.replace(" ", "") for string in user_ingredient if isinstance(string, str)]

for u in user_ingredient:
    if(u in ingredients_counts.keys()):
        if(ingredients_counts[u] >= threshold):
            user_ingredient_sparse_vector[sorted_ingredients_counts_list.index(u)] = (1 - ingredients_counts[u]/ingredients_origin_len)
    else:
        invalid_ingredients.append(u)


query_vector = pca.transform(np.array(list(user_ingredient_sparse_vector)).reshape(1, -1))

output = ', '.join(invalid_ingredients)
print(f'유효하지 않은 재료: {output}')

top_similar_recipes = get_top_similar_recipes(query_vector, ingredient_dense_vector_collect_dict, top_k=20)
top_similar_recipes

유효하지 않은 재료: 


[(6848869, 0.7559242510181818),
 (6899576, 0.7183913361786516),
 (6940677, 0.7097281019560135),
 (6871461, 0.7059205781573858),
 (6885502, 0.7036123695741858),
 (6862683, 0.7034836148265996),
 (6846518, 0.7015424851810876),
 (6830033, 0.6980390206164708),
 (6929886, 0.6958372809098856),
 (6644488, 0.6952544348307663),
 (6836004, 0.6937093445922498),
 (6925710, 0.6905730005488134),
 (6009195, 0.6845889156041647),
 (6981427, 0.6811737082207252),
 (6845918, 0.680782163877123),
 (6853690, 0.6785639590570058),
 (6923623, 0.6784576456245397),
 (6912047, 0.6782049030356991),
 (6930748, 0.6776904560469895),
 (6978283, 0.6776176776253624)]

In [ ]:
top_list = [x[0] for x in top_similar_recipes]
ingresync_recipe[ingresync_recipe['recipeid'].isin(top_list)]

recipeid                                title       cook quantity  \
2328     6862683                       삼삼(蔘蔘)한 삼계 영양찜        삼계찜      1인분   
8581     6009195                           알감자 닭고기 조림      닭감자조림      2인분   
13939    6644488                   삼시세끼 차승원따라잡기-제육볶음편       제육볶음      4인분   
21222    6978283                             실패없는김치찜♡        김치찜      4인분   
49698    6845918                      김치모짜렐라리조또&김치볶음밥  김치모짜렐라리조또      2인분   
50602    6846518                      봄소풍 샌드위치.아이올리소스       샌드위치      1인분   
64796    6930748                  집밥 쉬운 밑반찬 장조림 황금레시피        장조림      4인분   
65177    6923623     닭가슴살로 이탈리아 냄새가 물씬!!! 간단 치킨인볼티니 ★     치킨인볼티니      2인분   
68419    6836004                                제육볶음!       제육볶음      2인분   
70580    6830033                             제육볶음 만들기       제육볶음      2인분   
82089    6871461  버섯닭죽 만들기 양송이버섯 닭가슴살로 닭가슴살영양죽 만드는 방법       버섯닭죽      2인분   
84576    6848869                             치킨 시저샐러드    치킨시저샐러드      2인분   
93214    6940677                  정식품 진한 콩국물/ 콩국물 김치밥     콩국물김치밥      2인분   
93588    6853690  바베큐 치킨 파스타 (Barbeque chicken pasta)      치킨파스타      2인분   
96848    6912047                     가족모임에 좋은 불맛 제육볶음       제육볶음      4인분   
99587    6925710                           닭꼬치 만드는법~~        닭꼬치      4인분   
105655   6981427                          자취생 콜라수육만들기       콜라수육      2인분   
106569   6885502                          뷰코 코코넛 밀크 밥        밀크밥      2인분   
107023   6899576                            바질페스토 파스타   바질페스토파스타      2인분   
108921   6929886               돼지고기 삼겹살 덮밥 : 부타동 (豚丼)        부타동      2인분   

          time level                                        ingredients  \
2328    30분 이내    초급  [인삼, 닭가슴살, 대파 흰부분, 마늘, 대추, 건표고버섯, 소금, 간장, 설탕, ...   
8581    60분 이내    초급  [알감자, 닭가슴살, 마늘, 색색깔 청양고추, 간장, 설탕, 소금, 후추, 참기름,...   
13939   30분 이내    초급  [돼지고기, 양파, 대파, 중간크기 당근, 청양고추, 간장, 후추, 마늘, 간장, ...   
21222   30분 이내    중급        [묵은김치, 돼지고기, 육수, 대파, 고추가루, 설탕, 마늘, 맛술, 참기름]   
49698   30분 이내    초급  [쌀, 돼지고기, 양파, 베이컨, 청양고추, 모짜렐라치즈, 화이트와인, 치킨스톡물,...   
50602   15분 이내    초급  [닭가슴살, 청 겨자, 베트남고추, 생강, 할라피뇨, 마늘, 다시물, 간장, 설탕,...   
64796   30분 이내   아무나          [돼지고기, 후추, 대파, 양파, 간장, 소주, 설탕, 마늘, 고추, 물]   
65177   30분 이내   아무나  [닭가슴살, 스프링 치즈, 타임, 화이트와인, 토마토소스, 마늘, 소금, 후추, 올...   
68419   30분 이내    중급  [돼지고기, 양파, 대파, 땡초, 마늘, 고춧가루, 간장, 물엿, 설탕, 다진마늘,...   
70580   30분 이내    초급  [돼지고기, 마늘, 간장, 후추, 참기름돼지고기밑간용, 갈은양파, 고춧가루, 매실청...   
82089   60분 이내    초급                 [찹쌀, 마늘, 닭가슴살, 참기름, 간장, 소금, 양송이버섯]   
84576   60분 이내    중급  [닭가슴살, 베이컨, 양상추, 로메인, 올리브유, 소금, 후추, 제일제당시저드레싱 ...   
93214   60분 이내    초급    [쌀, 콩국물, 신김치, 돼지고기, 간장, 설탕, 마늘, 실파, 마늘생강오일, 후추]   
93588   15분 이내    초급  [펜네, 닭가슴살, 치킨텐더, 마늘, 양파, 토마토 소스, 바베큐 소스, 파마산 치...   
96848   30분 이내   아무나        [돼지고기, 양파, 대파, 고추, 마늘, 맛술, 식용유, 시판 돼지불고기양념]   
99587   20분 이내    초급     [닭가슴살, 대파, 고추장 수북히, 간장, 맛술, 청주, 케첩, 꿀, 마늘, 설탕]   
105655  60분 이내   아무나              [돼지고기, 양파, 마늘, 대파, 월계수잎, 콜라, 후추, 쌈채소]   
106569  60분 이내    초급  [양파, 뷰코 유기농 엑스트라버진 코코넛 오일, 뷰코 코코넛 밀크 프리미엄, 옥수수...   
107023  30분 이내    초급  [마늘, 새우, 베이컨, 닭가슴살, 새송이버섯 한, 파스타면, 올리브, 소금, 후추...   
108921  15분 이내   아무나            [돼지고기, 양파, 마늘, 잔파, 맛술, 청주, 간장, 간마늘, 생강]   

                                      ingredient_quantity  \
2328    [2뿌리(약60g), 1쪽(약150g), 10cm, 2쪽, 2개, 2장, 1/2밥숟...   
8581         [800g, 2개, , 4개, 3큰술, 1큰술, 1작은술, , , 1컵, 조금]   
13939   [800g, 1개, 1개, 1/3개, 3개, 3스푼, 약간, 2스푼, 3스푼, 7스...   
21222   [1/2포기, 300g, 3~4컵, 1/2쪽, 1~2T, 1/2T, 1T, 3T, 2T]   
49698   l, 150g, 1/5개, 1개, 1/2개, 6T, 1T, 200ml, 1...   
50602   [1/2개, 2장, 3개, 1T, 1개, 1개, 100ml, 1T, 1/2T, 1T...   
64796    [500g, 약간, 1개, 1/2개, 1/2컵, 1/3컵, 2T, 6알, 5개, 2컵]   
65177         [2장, 4개, 1줄기, 1/3종이컵, 1종이컵, 2알, 약간, 약간, 약간]   
68419   [500~600g, 1/2개, 2개, 2~3개, 5알, 2큰술, 2~3큰술, 1큰술...   
70580   [400g, 1, 1, , , 1개, 3큰술, 2큰술, 2, 1, 1, 1, 1, ...   
82089            [1/2컵, 2~3알, 먹을만큼, 2~3스푼, 1~2스푼, 조금, 조금]   
84576   [1 쪽, 1 장, 200 g, 100 g, 1 큰술,  약간,  약간, 적당량, ...   
93214   [300g, 500ml, 200g

In [ ]:
random_10 = random.sample(top_similar_recipes, k=10)
print(random_10)

[(6885502, 0.7036123695741858), (6925710, 0.6905730005488134), (6871461, 0.7059205781573858), (6846518, 0.7015424851810876), (6930748, 0.6776904560469895), (6929886, 0.6958372809098856), (6845918, 0.680782163877123), (6830033, 0.6980390206164708), (6853690, 0.6785639590570058), (6836004, 0.6937093445922498)]
